In [9]:
"""
Multi-Agent Dynamic Grid World Environment
Created by: Ardianto Wibowo
"""

import numpy as np
import sys
import random

# Add the path to the 'env' folder to sys.path
sys.path.append('env')

from ma_gridworld import Env
def add_noise(data, noise_type="color", noise_level=0.2):
    """
  
    """
    if noise_type == "location" and is_noise_enabled and enable_location_noise and random.random() < noise_level:
        return [
            max(0, min(data[0] + np.random.choice([-2, -1, 0, 1, 2]), min(env.WIDTH - 1, gsize - 1))),
            max(0, min(data[1] + np.random.choice([-2, -1, 0, 1, 2]), min(env.HEIGHT - 1, gsize - 1)))
        ]
    elif noise_type == "color" and is_noise_enabled and enable_color_noise and random.random() < noise_level:
    
        return f"target_{random.randint(0, 9)}" 
    return data


def evaluate_trust(agent_id, reported_by, is_correct, env):
    """
  
    """
    if is_correct:
        env.agent_trust_levels[reported_by] += 0.11  
        env.agent_trust_levels[reported_by] = min(env.agent_trust_levels[reported_by], 1.0)  # الحد الأعلى للثقة
        print(f"Agent {agent_id}: Trust in Agent {reported_by} increased to {env.agent_trust_levels[reported_by]}")
    else:
        env.agent_trust_levels[reported_by] -= 0.011 
        env.agent_trust_levels[reported_by] = max(env.agent_trust_levels[reported_by], 0.0)  # الحد الأدنى للثقة
        print(f"Agent {agent_id}: Trust in Agent {reported_by} decreased to {env.agent_trust_levels[reported_by]}")



class SearchAgent:
    def __init__(self, num_actions):
        self.num_actions = num_actions
        self.targets_seen = []
        self.memory = []  

        
        
    


    def analyse_sensor_data(self, agent_id, coordinate_observation, sensor_data_observation):
        for i in range(len(sensor_data_observation)):
            for j in range(len(sensor_data_observation[i])):
                data = sensor_data_observation[i][j]
                location = [coordinate_observation[0] + j - len(sensor_data_observation[i])//2,
                           coordinate_observation[1] + i - len(sensor_data_observation)//2]
                if data != None and 'target_' + str(agent_id) in data:
                    if location not in self.targets_seen:
                        self.targets_seen.append(location)
               
             
                   # evaluate_trust(agent_id, reported_by, is_correct, env)

            
           
                if data is not None and 'target_' + str(agent_id) in data:
                    if location not in self.targets_seen:
                        self.targets_seen.append(location)
                    self.update_memory(location, data, agent_id)

           
                if location[0] == coordinate_observation[0] and location[1] == coordinate_observation[1]:
                    if location in self.targets_seen:
                        self.targets_seen.remove(location)







    def analyse_communication(self, comm_observation, agent_id):
  
        for comm in comm_observation:
            origin_location = comm[0]
            sensor_data_observation = comm[1]
            reported_by = comm[2]

            print(f"Agent {agent_id}: Received communication from Agent {reported_by} at {origin_location}")

            for i in range(len(sensor_data_observation)):
                for j in range(len(sensor_data_observation[i])):
                    data = sensor_data_observation[i][j]
                    location = [
                        origin_location[0] + j - len(sensor_data_observation[i]) // 2,
                        origin_location[1] + i - len(sensor_data_observation) // 2
                    ]

                    
                 
                    if enable_location_noise:
                        location = add_noise(location, noise_type="location", noise_level=0.2)

                
                    if enable_color_noise and data is not None and "target_" in data:
                        data = add_noise(data, noise_type="color", noise_level=0.2)

             
                    if data is not None and 'target_' + str(agent_id) in data:
                        if location not in self.targets_seen:
                            self.targets_seen.append(location)
                            print(f"Agent {agent_id}: Added target from Agent {reported_by} at {location}")

                                 
                    if data is not None and 'target_' in data:
                        is_correct = self.verify_target(location, data, agent_id)
                        evaluate_trust(agent_id, reported_by, is_correct, env)

    def update_memory(self, location, data, agent_id):
        """
     
        """
        if location not in [record["location"] for record in self.memory]:
            self.memory.append({"location": location, "data": data})
            print(f"Agent {agent_id}: Updated Memory: {location} -> {data}")


                
    def verify_target(self, location, data, agent_id):
        """
       
        """
        print(f"Verifying target at {location} with data {data} for Agent {agent_id}")
        for record in self.memory:
            if record["location"] == location and record["data"] == data:
                print(f"Agent {agent_id}: Verified target at {location} as correct.")
                return True
        print(f"Agent {agent_id}: Verified target at {location} as incorrect.")
        return False



    def select_action(self, coordinate_observation, agent_id):
        print(f"Agent {agent_id}: Current targets seen: {self.targets_seen}")
        if len(self.targets_seen) > 0:
            closest_target = None
            closest_target_distance = 999999
            for target_coordinate in self.targets_seen:
                horizontal_distance = target_coordinate[0] - coordinate_observation[0]
                vertical_distance = target_coordinate[1] - coordinate_observation[1]
                distance = abs(horizontal_distance) + abs(vertical_distance)
                if distance < closest_target_distance:
                    closest_target_distance = distance
                    closest_target = target_coordinate

            if closest_target:
                print(f"Agent {agent_id}: Moving towards target at {closest_target}")
                horizontal_distance = closest_target[0] - coordinate_observation[0]
                vertical_distance = closest_target[1] - coordinate_observation[1]
                if abs(horizontal_distance) >= abs(vertical_distance):
                    return 3 if horizontal_distance < 0 else 4
                else:
                    return 1 if vertical_distance < 0 else 2
        else:
            print(f"Agent {agent_id}: No targets seen, taking random action.")
            return np.random.choice(self.num_actions - 1) + 1





def get_action(agent_id, observation, num_actions, agents, env):
    """
    This method provides a random action chosen recognized by the ma-gridworld environment:
    1: up, 2: down, 3: left, 4: right, 0: stay
    """
    
    coordinate_observation = tuple(observation[0])  # Keep observation as (x, y) tuple

    # Optional observation data may be used, depend on the agent needs.
    win_state_observation = observation[1]
    sensor_data_observation = observation[2]
    comm_observation = observation[3]
    

    #print(f"Observation for Agent {agent_id}: {observation}")

    # Check if communication data is available
    if comm_observation:
        agents[agent_id].analyse_communication(comm_observation, agent_id)
    else:
        print(f"Agent {agent_id}: No communication data available this step.")

    # Analyze sensor data
    agents[agent_id].analyse_sensor_data(agent_id, coordinate_observation, sensor_data_observation)
    
    # Select physical action
    physical_action = agents[agent_id].select_action(coordinate_observation, agent_id)

    # Define communication action
    if env.is_agent_silent:
        comm_action = []  # Communication action is set to be zero if agent silent
    else:
      
        noisy_location = add_noise(coordinate_observation, noise_type="location", noise_level=0.2)
        comm_action = [noisy_location, sensor_data_observation, agent_id]

    return (physical_action, comm_action)


def run(num_episodes, max_steps_per_episode, agents, num_actions, env):
    for episode in range(num_episodes):
        print(f"Starting episode {episode + 1}")
        observations = env.reset()  # Reset the environment at the start of each episode
        
        for agent in agents:
            agent.__init__(num_actions)
            
        print("Initial Trust Levels for Agents:")
        for agent_id, trust_level in enumerate(env.agent_trust_levels):
            print(f"Agent {agent_id}: Trust Level = {trust_level}")
        
        if enable_trust_evaluation:
            print("Trust Levels after Step:")
            for agent_id, trust_level in enumerate(env.agent_trust_levels):
                print(f"  Agent {agent_id}: Trust Level = {trust_level}")

        done = [False] * env.num_agents  # Initialize 'done' as a list for each agent
        step_count = 0

        while not all(done) and step_count < max_steps_per_episode:  # Stop if all agents are done or max steps reached
            actions = []
            next_observations = []
            
            for agent_id in range(env.num_agents):
                observation = observations[agent_id]
                action = get_action(agent_id, observation, num_actions, agents, env)
                
                actions.append(action)
                next_observations.append(observation)

            next_observations, rewards, done = env.step(actions)  # Step in the environment

            observations = next_observations
            step_count += 1

            # Render the environment
            env.render()

        
            print(f"Step {step_count}:")
            for agent_id in range(env.num_agents):
                print(
                    f"  Agent {agent_id}: Observation: {observations[agent_id]}, "
                    f"Action: {actions[agent_id]}, Reward: {rewards[agent_id]}, Done: {done[agent_id]}"
                )

  
        print(f"Episode {episode + 1} finished after {step_count} steps.\n")
        for agent_id, trust_level in enumerate(env.agent_trust_levels):
            print(f"Agent {agent_id}: Trust Level = {trust_level}")




if __name__ == "__main__":

    gsize=20 #grid size (square)
    gpixels=30 #grid cell size in pixels

    is_sensor_active = True #True:  Activate the sensory observation data
    sensory_size = 3 #'is_sensor_active' must be True. The value must be odd, if event will be converted to one level odd number above
    
    num_agents = 10 #the number of agents will be run in paralel
    num_obstacles = 0 #the number of obstacles
    is_single_target = False #True: all agents have a single target, False: each agent has their own target
    num_targets_per_agent = 8 #'is_single_target' must be true to have an effect
    
    is_agent_silent = False #True: communication among agents is allowed
    
    
    is_noise_enabled = False 
   
    enable_location_noise = False 
    enable_color_noise = True 

    noise_level = 0.2  
   

        
    enable_trust_evaluation = True

    num_episodes=1 #the number of episode will be run
    max_steps_per_episode=1000 #each episode will be stopped when max_step is reached

    eps_moving_targets = 10 #set this value greater than 'num_episodes' to keep the targets in a stationary position
    eps_moving_obstacles = 10 #set this value greater than 'num_episodes' to keep the obstacles in a stationary position

    render = True #True: render the animation into the screen (so far, it is still can not be deactivated)

    min_obstacle_distance_from_target = 1 #min grid distance of each obstacles relative to targets
    max_obstacle_distance_from_target = 5 #max grid distance of each obstacles relative to targets
    min_obstacle_distance_from_agents = 1 #min grid distance of each obstacles relative to agents

    reward_normal = -1 #reward value of normal steps
    reward_obstacle = -5 #reward value when hit an obstacle
    reward_target = 50 #reward value when reach the target

    is_totally_random = True #True: target and obstacles initial as well as movement position is always random on each call, False: only random at the beginning. 
    animation_speed = 0.1 #smaller is faster 
    is_destroy_environment = True #True: automatically close the animation after all episodes end.  

    # Initialize environment
    env = Env(
        num_agents=num_agents, num_targets_per_agent=num_targets_per_agent, num_obstacles=num_obstacles,
        eps_moving_obstacles=eps_moving_obstacles, eps_moving_targets=eps_moving_targets,
        is_agent_silent=is_agent_silent, is_single_target=is_single_target, sensory_size=sensory_size,
        gpixels=gpixels, gheight=gsize, gwidth=gsize, is_sensor_active=is_sensor_active,
        min_obstacle_distance_from_target=min_obstacle_distance_from_target,
        max_obstacle_distance_from_target=max_obstacle_distance_from_target,
        min_obstacle_distance_from_agents=min_obstacle_distance_from_agents,
        is_totally_random=is_totally_random, animation_speed=animation_speed,
        reward_normal=reward_normal, reward_obstacle=reward_obstacle, reward_target=reward_target
    )
    
    num_actions = len(env.action_space)
    
    # Initialize Q-learning agents
    agents = [SearchAgent(num_actions) for _ in range(num_agents)]

    # Run episodes
    run(num_episodes, max_steps_per_episode, agents, num_actions, env)

    if is_destroy_environment:
        env.destroy_environment() 


Starting episode 1
Initial Trust Levels for Agents:
Agent 0: Trust Level = 0.47
Agent 1: Trust Level = 0.3
Agent 2: Trust Level = 0.37
Agent 3: Trust Level = 0.64
Agent 4: Trust Level = 1.0
Agent 5: Trust Level = 0.25
Agent 6: Trust Level = 0.35
Agent 7: Trust Level = 0.65
Agent 8: Trust Level = 0.43
Agent 9: Trust Level = 0.74
Trust Levels after Step:
  Agent 0: Trust Level = 0.47
  Agent 1: Trust Level = 0.3
  Agent 2: Trust Level = 0.37
  Agent 3: Trust Level = 0.64
  Agent 4: Trust Level = 1.0
  Agent 5: Trust Level = 0.25
  Agent 6: Trust Level = 0.35
  Agent 7: Trust Level = 0.65
  Agent 8: Trust Level = 0.43
  Agent 9: Trust Level = 0.74
Agent 0: No communication data available this step.
Agent 0: Current targets seen: []
Agent 0: No targets seen, taking random action.
Agent 1: No communication data available this step.
Agent 1: Current targets seen: []
Agent 1: No targets seen, taking random action.
Agent 2: No communication data available this step.
Agent 2: Current targets se

Step 2:
  Agent 0: Observation: [[2, 0], False, [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], [[(19, 0), [[None, None, None], ['empty', 'agent', None], ['empty', 'empty', None]], 1], [(19, 19), [['target_3_1', 'empty', None], ['empty', 'agent', None], [None, None, None]], 2], [(0, 19), [[None, 'empty', 'empty'], [None, 'agent', 'empty'], [None, None, None]], 3], [(6, 1), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['target_1_3', 'target_6_4', 'empty']], 4], [(12, 0), [[None, None, None], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 5], [(19, 5), [['target_5_0', 'empty', None], ['target_3_6', 'empty', None], ['target_4_2', 'agent', None]], 6], [(18, 13), [['empty', 'target_0_2', 'empty'], ['target_3_3', 'target_5_7', 'agent'], ['empty', 'empty', 'empty']], 7], [(10, 19), [['empty', 'empty', 'empty'], ['empty', 'agent', 'empty'], [None, None, None]], 8], [(1, 10), [['empty', 'empty', 'empty'], ['agent', 'empty', 'target_4_7']

Step 4:
  Agent 0: Observation: [[3, 1], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['target_0_0', 'target_9_0', 'target_8_0']], [[(18, 0), [[None, None, None], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 1], [(18, 19), [['empty', 'target_3_1', 'empty'], ['empty', 'empty', 'agent'], [None, None, None]], 2], [(2, 19), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], [None, None, None]], 3], [(7, 2), [['empty', 'agent', 'empty'], ['target_6_4', 'empty', 'empty'], ['empty', 'empty', 'empty']], 4], [(13, 1), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 5], [(18, 6), [['target_7_4', 'target_3_6', 'empty'], ['empty', 'target_4_2', 'agent'], ['empty', 'empty', 'empty']], 6], [(19, 14), [['target_5_7', 'empty', None], ['agent', 'empty', None], ['empty', 'empty', None]], 7], [(12, 19), [['empty', 'empty', 'target_5_6'], ['agent', 'empty', 'empty'], [None, None, None]], 8], [(1, 8), [['empty', 'empty', 'e

Step 6:
  Agent 0: Observation: [[2, 2], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'target_9_0'], ['empty', 'empty', 'empty']], [[(16, 0), [[None, None, None], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 1], [(19, 19), [['target_3_1', 'empty', None], ['agent', 'empty', None], [None, None, None]], 2], [(4, 19), [['empty', 'target_6_7', 'empty'], ['agent', 'empty', 'empty'], [None, None, None]], 3], [(7, 4), [['empty', 'agent', 'empty'], ['empty', 'target_6_5', 'empty'], ['empty', 'empty', 'target_7_1']], 4], [(15, 1), [['empty', 'empty', 'agent'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 5], [(16, 6), [['empty', 'empty', 'target_7_4'], ['empty', 'empty', 'agent'], ['empty', 'target_9_1', 'empty']], 6], [(19, 14), [['target_5_7', 'empty', None], ['empty', 'empty', None], ['empty', 'agent', None]], 7], [(11, 19), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], [None, None, None]], 8], [(0, 7), [[None, 'empty', 'empty'], [None, 'emp

Step 8:
  Agent 0: Observation: [[2, 4], False, [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], [[(14, 0), [[None, None, None], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 1], [(18, 18), [['empty', 'empty', 'empty'], ['empty', 'target_3_1', 'empty'], ['empty', 'agent', 'empty']], 2], [(6, 19), [['empty', 'empty', 'target_7_7'], ['agent', 'empty', 'empty'], [None, None, None]], 3], [(7, 6), [['empty', 'agent', 'target_7_1'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 4], [(16, 2), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['target_3_0', 'empty', 'target_9_6']], 5], [(14, 6), [['target_1_4', 'empty', 'empty'], ['empty', 'target_3_4', 'agent'], ['empty', 'empty', 'empty']], 6], [(19, 12), [['empty', 'empty', None], ['target_0_1', 'empty', None], ['target_5_7', 'agent', None]], 7], [(11, 17), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 8], [(0, 5), [[None, '

...

Step 238:
  Agent 0: Observation: [[5, 12], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], [[(16, 3), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 1], [(18, 19), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], [None, None, None]], 2], [(0, 1), [[None, 'agent', 'empty'], [None, 'empty', 'empty'], [None, 'empty', 'empty']], 3], [(8, 13), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 4], [(8, 2), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 5], [(17, 13), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 6], [(8, 7), [['empty', 'empty', 'empty'], ['empty', 'agent', 'agent'], ['empty', 'empty', 'empty']], 7], [(8, 6), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 8], [(6, 16), [['empty', 'empty', 'empty'], ['empty', 'empt

Step 240:
  Agent 0: Observation: [[4, 13], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], [[(15, 2), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 1], [(17, 18), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 2], [(0, 3), [[None, 'agent', 'empty'], [None, 'empty', 'empty'], [None, 'empty', 'empty']], 3], [(9, 12), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 4], [(7, 1), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 5], [(16, 14), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 6], [(8, 9), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 7], [(7, 5), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 8], [(6, 16), [['empty', 'empty', 'empty'], ['empt

Step 242:
  Agent 0: Observation: [[3, 12], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], [[(16, 1), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 1], [(17, 16), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 2], [(1, 2), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 3], [(9, 12), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 4], [(7, 1), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 5], [(16, 14), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 6], [(9, 10), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 7], [(6, 4), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 8], [(6, 14), [['empty', 'empty', 'empty

Step 244:
  Agent 0: Observation: [[2, 11], False, [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], [[(15, 0), [[None, None, None], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 1], [(18, 15), [['agent', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 2], [(1, 2), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 3], [(8, 13), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 4], [(8, 0), [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 5], [(18, 14), [['empty', 'empty', 'empty'], ['agent', 'empty', 'empty'], ['empty', 'agent', 'empty']], 6], [(9, 10), [['empty', 'empty', 'empty'], ['empty', 'empty', 'agent'], ['empty', 'empty', 'empty']], 7], [(5, 3), [['target_8_0', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 8], [(6, 12), [['empty', 'empty', 'empty'], ['empty',

Step 246:
  Agent 0: Observation: [[3, 10], True, [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], [[(15, 2), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 1], [(18, 17), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 2], [(2, 1), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 3], [(6, 13), [['empty', 'empty', 'empty'], ['empty', 'agent', 'agent'], ['empty', 'empty', 'empty']], 4], [(10, 0), [[None, None, None], ['agent', 'empty', 'empty'], ['empty', 'empty', 'empty']], 5], [(18, 14), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 6], [(9, 10), [['empty', 'agent', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'empty', 'empty']], 7], [(4, 2), [['empty', 'empty', 'empty'], ['empty', 'empty', 'empty'], ['empty', 'agent', 'empty']], 8], [(5, 13), [['empty', 'empty', 'empty'], ['emp